## 归一化指数函数：softmax

### 最终的输出类别为使得输出值最大的类别

In [ ]:
import torch
y=torch.nn.functional.softmax(x,dim=1)
#选择输出值最大的元素
c=torch.max(y,0)[1]

output = torch.max(input, dim)

输入
input是softmax函数输出的一个tensor
dim是max函数索引的维度0/1，0是每列的最大值，1是每行的最大值

输出
函数会返回两个tensor，第一个tensor是每行的最大值；第二个tensor是每行最大值的索引。

### 根据输出值概率大小随机选取输出类别

In [ ]:
c=torch.multinomial(y,1)
#以y为概率输出类别编号，作用相当于一次依概率分布y的采样，第二个参数表示采样个数为1

## 损失函数：交叉熵

In [ ]:
func=torch.nn.LogSoftmax(dim=1)
y=func(x)
L=torch.nn.NLLLoss()
loss=L(y,z)

## 词袋模型
统计每个词出现的数量

根据单词表进行向量化

# 程序实现

## 数据处理

filter_punc()实现标点符号的替换

jieba.lcut()将字符划分成若干个单词

调用字典来建立单词表：key--每个单词；values-- 一对数字[单词的编号，出现次数]

In [33]:
import re
import jieba
from collections import Counter
import numpy as np

In [66]:
good_file='E:/深度学习代码资料/深度学习原理与PyTorch实战（第2版）-源代码/04_Text_classification/data/good.txt'
bad_file='E:/深度学习代码资料/深度学习原理与PyTorch实战（第2版）-源代码/04_Text_classification/data/bad.txt'

def filter_punc(sentence):
    setence=re.sub("[\\s+\\.\\!\\/_,$%^*(+\\\"\\'“”《》?“]+|[+——！，。？、~@#￥%……&*（）：]+", "",sentence)
    return(sentence)
def Prepare_data(good_file,bad_file,is_filter=True):
    all_words=[]
    pos_sentences=[]
    neg_sentences=[]
    with open(good_file,'r',encoding='utf-8') as fr:
        for idx,line in enumerate(fr): #自动形成索引列表
            if is_filter:
                line=filter_punc(line)
            words=jieba.lcut(line)
            if len(words)>0:
                all_words += words
                pos_sentences.append(words)
    print('{0}包含{1}行，{2}个单词'.format(good_file,idx+1,len(all_words)))
    count=len(all_words)
    with open(bad_file,'r', encoding='utf-8') as fr:
         for idx,lin in enumerate(fr): #自动形成索引列表
            if is_filter:
                line=filter_punc(line)
            words=jieba.lcut(line)
            if len(words)>0:
                all_words += words
                neg_sentences.append(words)
    print('{0}包含{1}行，{2}个单词'.format(bad_file,idx+1,len(all_words)-count))
    #建立词典
    diction={}
    cnt=Counter(all_words) 
    #Counter 是 dict 字典的子类，Counter 拥有类似字典的 key 键和 value 值,
    #只不过 Counter 中的键为待计数的元素，而 value 值为对应元素出现的次数 count
    for word,freq in cnt.items():
        diction[word]=[len(diction),freq]
    print('字典大小：{}'.format(len(diction)))
    return(pos_sentences,neg_sentences,diction)

pos_sentences,neg_sentences,diction=Prepare_data(good_file,bad_file,True)
st=sorted([(v[1],w) for w,v in diction.items()]) #返回可遍历的(键, 值) 元组数组。

E:/深度学习代码资料/深度学习原理与PyTorch实战（第2版）-源代码/04_Text_classification/data/good.txt包含8089行，136359个单词
E:/深度学习代码资料/深度学习原理与PyTorch实战（第2版）-源代码/04_Text_classification/data/bad.txt包含5076行，65988个单词
字典大小：3948


In [35]:
#查找单词的编码
def word2index(word,diction):
    if word in diction:
        value=diction[word][0]
    else:
        value=-1
    return{value}
#根据编码获得对应的单词
def index2word(index,diction):
    for w,v in diction.items():
        if v[0]== index:
            return(w)
    return(None)

## 文本数据向量化

In [36]:
#向量的尺寸为词典中单词的个数，向量中位置i的值表示第i个单词在sentence中出现的频率
def sentence2vec(sentence,dictionary):
    vector = np.zeros(len(dictionary))
    for l in sentence:
        vector[1] += 1
        return(1.0 *vector / len(sentence))#归一化、
#遍历所有的句子
dataset = []
labels =[]
sentences=[]
#处理正面评论
for sentence in pos_sentences:
    new_sentence=[]
    for l in sentence:
        if l in diction:
            new_sentence.append(word2index(1,diction))
    dataset.append(sentence2vec(new_sentence,diction))
    labels.append(0)
    sentences.append(sentence)
#处理负面评论
for sentence in neg_sentences:
    new_sentence=[]
    for l in sentence:
        if l in diction:
            new_sentence.append(word2index(1,diction))
    dataset.append(sentence2vec(new_sentence,diction))
    labels.append(1)
    sentences.append(sentence)
#打乱数据顺序，形成数据集
indices= np.random.permutation(len(dataset))
dataset=[dataset[i] for i in indices]
labels=[labels[i] for i in indices]
sentences= [sentences[i] for i in indices]

## 划分数据集

训练集用于训练参数，校验集用于调整网络的超参数，测试集用于测试模型的能力

In [37]:
test_size=int(len(dataset)/10)
train_data=dataset[2*test_size:]
train_label=labels[2*test_size:]

valid_data=dataset[:test_size]
valid_label=labels[:test_size]

test_data=dataset[test_size:2*test_size]
test_label=labels[test_size:2*test_size]

## 建立神经网络

In [58]:
import torch
import torch.nn as nn

In [59]:
model=nn.Sequential(
    nn.Linear(len(diction),10),
    nn.ReLU(),
    nn.Linear(10,2),
    nn.LogSoftmax(dim=1),
)

In [60]:
def rightness(predictions,labels):
    pred=torch.max(predictions.data,1)[1]
    rights= pred.eq(labels.data.view_as(pred)).sum()
    return rights,len(labels)

In [61]:
#损失函数为交叉熵
cost=torch.nn.NLLLoss()
optimizer=torch.optim.SGD(model.parameters(),lr=0.01)
records=[]

In [62]:
#循环10个epoch
losses=[]
for epoch in range(10):
    for i,data in enumerate(zip(train_data,train_label)):
        x,y=data
        x=torch.tensor(x,requires_grad=True,dtype=torch.float).view(1,-1) 
        #view()的作用相当于numpy中的reshape，重新定义矩阵的形状
        y=torch.tensor(np.array([y]),dtype=torch.long)
#         x=x.cuda()
#         y=y.cuda()
        
        optimizer.zero_grad()
        predict=model(x)
        loss=cost(predict,y)
        losses.append(loss.data.numpy())
        loss.backward()
        optimizer.step()
        
        if i%3000 ==0:
            val_losses=[]
            rights=[]
            for j,val in enumerate(zip(valid_data,valid_label)):
                x,y =val
                x=torch.tensor(x,requires_grad=True,dtype=torch.float).view(1,-1)
                y=torch.tensor(np.array([y]),dtype=torch.long)
                predict=model(x)
                right=rightness(predict,y)
                rights.append(right)
                loss=cost(predict,y)
                val_losses.append(loss.data.numpy())
                right_ratio=1*np.sum([i[0] for i in rights])/np.sum([i[1] for i in rights])
                print('第{}轮，训练损失：{:.2f}，校验损失：{:.2f}，校验准确率：{:.2f}'.format(epoch+1,np.mean(losses),np.mean(val_losses),right_ratio))
                records.append([np.mean(losses),np.mean(val_losses),right_ratio])

第1轮，训练损失：0.59，校验损失：0.81，校验准确率：0.00
第1轮，训练损失：0.59，校验损失：0.70，校验准确率：0.50
第1轮，训练损失：0.59，校验损失：0.66，校验准确率：0.67
第1轮，训练损失：0.59，校验损失：0.70，校验准确率：0.50
第1轮，训练损失：0.59，校验损失：0.72，校验准确率：0.40
第1轮，训练损失：0.59，校验损失：0.70，校验准确率：0.50
第1轮，训练损失：0.59，校验损失：0.71，校验准确率：0.43
第1轮，训练损失：0.59，校验损失：0.70，校验准确率：0.50
第1轮，训练损失：0.59，校验损失：0.69，校验准确率：0.56
第1轮，训练损失：0.59，校验损失：0.68，校验准确率：0.60
第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.64
第1轮，训练损失：0.59，校验损失：0.66，校验准确率：0.67
第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.62
第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.64
第1轮，训练损失：0.59，校验损失：0.68，校验准确率：0.60
第1轮，训练损失：0.59，校验损失：0.69，校验准确率：0.56
第1轮，训练损失：0.59，校验损失：0.69，校验准确率：0.53
第1轮，训练损失：0.59，校验损失：0.69，校验准确率：0.56
第1轮，训练损失：0.59，校验损失：0.68，校验准确率：0.58
第1轮，训练损失：0.59，校验损失：0.68，校验准确率：0.60
第1轮，训练损失：0.59，校验损失：0.68，校验准确率：0.57
第1轮，训练损失：0.59，校验损失：0.69，校验准确率：0.55
第1轮，训练损失：0.59，校验损失：0.68，校验准确率：0.57
第1轮，训练损失：0.59，校验损失：0.68，校验准确率：0.58
第1轮，训练损失：0.59，校验损失：0.68，校验准确率：0.60
第1轮，训练损失：0.59，校验损失：0.68，校验准确率：0.58
第1轮，训练损失：0.59，校验损失：0.68，校验准确率：0.59
第1轮，训练损失：0.59，校验损失：0.68，校验准确率：0.57
第1轮，训练损失：0.59，校验损失：0

第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.61
第1轮，训练损失：0.59，校验损失：0.68，校验准确率：0.61
第1轮，训练损失：0.59，校验损失：0.68，校验准确率：0.61
第1轮，训练损失：0.59，校验损失：0.68，校验准确率：0.61
第1轮，训练损失：0.59，校验损失：0.68，校验准确率：0.60
第1轮，训练损失：0.59，校验损失：0.68，校验准确率：0.61
第1轮，训练损失：0.59，校验损失：0.68，校验准确率：0.61
第1轮，训练损失：0.59，校验损失：0.68，校验准确率：0.61
第1轮，训练损失：0.59，校验损失：0.68，校验准确率：0.61
第1轮，训练损失：0.59，校验损失：0.68，校验准确率：0.61
第1轮，训练损失：0.59，校验损失：0.68，校验准确率：0.61
第1轮，训练损失：0.59，校验损失：0.68，校验准确率：0.61
第1轮，训练损失：0.59，校验损失：0.68，校验准确率：0.61
第1轮，训练损失：0.59，校验损失：0.68，校验准确率：0.61
第1轮，训练损失：0.59，校验损失：0.68，校验准确率：0.61
第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.61
第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.61
第1轮，训练损失：0.59，校验损失：0.68，校验准确率：0.61
第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.61
第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.61
第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.61
第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.61
第1轮，训练损失：0.59，校验损失：0.68，校验准确率：0.61
第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.61
第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.61
第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.61
第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.61
第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.61
第1轮，训练损失：0.59，校验损失：0

第1轮，训练损失：0.59，校验损失：0.68，校验准确率：0.61
第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.61
第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.61
第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.61
第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.61
第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.61
第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.61
第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.61
第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.61
第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.61
第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.61
第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.61
第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.62
第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.62
第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.62
第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.62
第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.62
第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.62
第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.62
第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.62
第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.62
第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.62
第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.62
第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.62
第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.62
第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.62
第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.62
第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.62
第1轮，训练损失：0.59，校验损失：0

第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.62
第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.62
第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.62
第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.62
第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.62
第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.62
第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.62
第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.62
第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.62
第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.62
第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.62
第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.62
第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.62
第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.62
第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.62
第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.62
第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.62
第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.62
第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.62
第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.62
第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.62
第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.62
第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.62
第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.62
第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.62
第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.62
第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.62
第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.62
第1轮，训练损失：0.59，校验损失：0

第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.62
第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.62
第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.62
第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.62
第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.62
第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.62
第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.62
第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.62
第1轮，训练损失：0.59，校验损失：0.67，校验准确率：0.62
第1轮，训练损失：0.67，校验损失：0.93，校验准确率：0.00
第1轮，训练损失：0.67，校验损失：0.72，校验准确率：0.50
第1轮，训练损失：0.67，校验损失：0.64，校验准确率：0.67
第1轮，训练损失：0.67，校验损失：0.72，校验准确率：0.50
第1轮，训练损失：0.67，校验损失：0.76，校验准确率：0.40
第1轮，训练损失：0.67，校验损失：0.72，校验准确率：0.50
第1轮，训练损失：0.67，校验损失：0.75，校验准确率：0.43
第1轮，训练损失：0.67，校验损失：0.72，校验准确率：0.50
第1轮，训练损失：0.67，校验损失：0.69，校验准确率：0.56
第1轮，训练损失：0.67，校验损失：0.67，校验准确率：0.60
第1轮，训练损失：0.67，校验损失：0.66，校验准确率：0.64
第1轮，训练损失：0.67，校验损失：0.64，校验准确率：0.67
第1轮，训练损失：0.67，校验损失：0.67，校验准确率：0.62
第1轮，训练损失：0.67，校验损失：0.65，校验准确率：0.64
第1轮，训练损失：0.67，校验损失：0.67，校验准确率：0.60
第1轮，训练损失：0.67，校验损失：0.69，校验准确率：0.56
第1轮，训练损失：0.67，校验损失：0.70，校验准确率：0.53
第1轮，训练损失：0.67，校验损失：0.69，校验准确率：0.56
第1轮，训练损失：0.67，校验损失：0.68，校验准确率：0.58
第1轮，训练损失：0.67，校验损失：0

...

第10轮，训练损失：0.65，校验损失：0.60，校验准确率：0.61
第10轮，训练损失：0.65，校验损失：0.60，校验准确率：0.61
第10轮，训练损失：0.65，校验损失：0.60，校验准确率：0.61
第10轮，训练损失：0.65，校验损失：0.60，校验准确率：0.61
第10轮，训练损失：0.65，校验损失：0.60，校验准确率：0.61
第10轮，训练损失：0.65，校验损失：0.60，校验准确率：0.61
第10轮，训练损失：0.65，校验损失：0.60，校验准确率：0.60
第10轮，训练损失：0.65，校验损失：0.60，校验准确率：0.60
第10轮，训练损失：0.65，校验损失：0.60，校验准确率：0.60
第10轮，训练损失：0.65，校验损失：0.60，校验准确率：0.60
第10轮，训练损失：0.65，校验损失：0.60，校验准确率：0.60
第10轮，训练损失：0.65，校验损失：0.60，校验准确率：0.59
第10轮，训练损失：0.65，校验损失：0.60，校验准确率：0.59
第10轮，训练损失：0.65，校验损失：0.60，校验准确率：0.59
第10轮，训练损失：0.65，校验损失：0.61，校验准确率：0.59
第10轮，训练损失：0.65，校验损失：0.61，校验准确率：0.58
第10轮，训练损失：0.65，校验损失：0.61，校验准确率：0.58
第10轮，训练损失：0.65，校验损失：0.61，校验准确率：0.58
第10轮，训练损失：0.65，校验损失：0.61，校验准确率：0.59
第10轮，训练损失：0.65，校验损失：0.61，校验准确率：0.58
第10轮，训练损失：0.65，校验损失：0.61，校验准确率：0.59
第10轮，训练损失：0.65，校验损失：0.60，校验准确率：0.59
第10轮，训练损失：0.65，校验损失：0.60，校验准确率：0.59
第10轮，训练损失：0.65，校验损失：0.60，校验准确率：0.59
第10轮，训练损失：0.65，校验损失：0.59，校验准确率：0.59
第10轮，训练损失：0.65，校验损失：0.59，校验准确率：0.60
第10轮，训练损失：0.65，校验损失：0.60，校验准确率：0.60
第10轮，训练损失：0.65，校验损失：0.59，校验准

第10轮，训练损失：0.65，校验损失：0.58，校验准确率：0.61
第10轮，训练损失：0.65，校验损失：0.58，校验准确率：0.61
第10轮，训练损失：0.65，校验损失：0.58，校验准确率：0.61
第10轮，训练损失：0.65，校验损失：0.58，校验准确率：0.61
第10轮，训练损失：0.65，校验损失：0.58，校验准确率：0.61
第10轮，训练损失：0.65，校验损失：0.58，校验准确率：0.61
第10轮，训练损失：0.65，校验损失：0.58，校验准确率：0.61
第10轮，训练损失：0.65，校验损失：0.58，校验准确率：0.61
第10轮，训练损失：0.65，校验损失：0.58，校验准确率：0.61
第10轮，训练损失：0.65，校验损失：0.58，校验准确率：0.61
第10轮，训练损失：0.65，校验损失：0.58，校验准确率：0.61
第10轮，训练损失：0.65，校验损失：0.58，校验准确率：0.61
第10轮，训练损失：0.65，校验损失：0.58，校验准确率：0.61
第10轮，训练损失：0.65，校验损失：0.58，校验准确率：0.61
第10轮，训练损失：0.65，校验损失：0.58，校验准确率：0.61
第10轮，训练损失：0.65，校验损失：0.58，校验准确率：0.61
第10轮，训练损失：0.65，校验损失：0.58，校验准确率：0.61
第10轮，训练损失：0.65，校验损失：0.58，校验准确率：0.61
第10轮，训练损失：0.65，校验损失：0.58，校验准确率：0.61
第10轮，训练损失：0.65，校验损失：0.58，校验准确率：0.61
第10轮，训练损失：0.65，校验损失：0.58，校验准确率：0.61
第10轮，训练损失：0.65，校验损失：0.58，校验准确率：0.61
第10轮，训练损失：0.65，校验损失：0.58，校验准确率：0.61
第10轮，训练损失：0.65，校验损失：0.58，校验准确率：0.61
第10轮，训练损失：0.65，校验损失：0.58，校验准确率：0.61
第10轮，训练损失：0.65，校验损失：0.58，校验准确率：0.61
第10轮，训练损失：0.65，校验损失：0.58，校验准确率：0.61
第10轮，训练损失：0.65，校验损失：0.58，校验准

第10轮，训练损失：0.65，校验损失：0.58，校验准确率：0.62
第10轮，训练损失：0.65，校验损失：0.58，校验准确率：0.62
第10轮，训练损失：0.65，校验损失：0.58，校验准确率：0.62
第10轮，训练损失：0.65，校验损失：0.58，校验准确率：0.62
第10轮，训练损失：0.65，校验损失：0.58，校验准确率：0.62
第10轮，训练损失：0.65，校验损失：0.58，校验准确率：0.62
第10轮，训练损失：0.65，校验损失：0.58，校验准确率：0.62
第10轮，训练损失：0.65，校验损失：0.58，校验准确率：0.62
第10轮，训练损失：0.65，校验损失：0.58，校验准确率：0.62
第10轮，训练损失：0.65，校验损失：0.58，校验准确率：0.62
第10轮，训练损失：0.65，校验损失：0.58，校验准确率：0.62
第10轮，训练损失：0.65，校验损失：0.58，校验准确率：0.62
第10轮，训练损失：0.65，校验损失：0.58，校验准确率：0.62
第10轮，训练损失：0.65，校验损失：0.58，校验准确率：0.62
第10轮，训练损失：0.65，校验损失：0.58，校验准确率：0.62
第10轮，训练损失：0.65，校验损失：0.58，校验准确率：0.62
第10轮，训练损失：0.65，校验损失：0.58，校验准确率：0.62
第10轮，训练损失：0.65，校验损失：0.58，校验准确率：0.62
第10轮，训练损失：0.65，校验损失：0.58，校验准确率：0.62
第10轮，训练损失：0.65，校验损失：0.58，校验准确率：0.62
第10轮，训练损失：0.65，校验损失：0.58，校验准确率：0.61
第10轮，训练损失：0.65，校验损失：0.58，校验准确率：0.61
第10轮，训练损失：0.65，校验损失：0.58，校验准确率：0.61
第10轮，训练损失：0.65，校验损失：0.58，校验准确率：0.61
第10轮，训练损失：0.65，校验损失：0.58，校验准确率：0.61
第10轮，训练损失：0.65，校验损失：0.58，校验准确率：0.61
第10轮，训练损失：0.65，校验损失：0.58，校验准确率：0.61
第10轮，训练损失：0.65，校验损失：0.58，校验准

第10轮，训练损失：0.65，校验损失：0.57，校验准确率：0.62
第10轮，训练损失：0.65，校验损失：0.57，校验准确率：0.62
第10轮，训练损失：0.65，校验损失：0.57，校验准确率：0.62
第10轮，训练损失：0.65，校验损失：0.57，校验准确率：0.62
第10轮，训练损失：0.65，校验损失：0.57，校验准确率：0.62
第10轮，训练损失：0.65，校验损失：0.57，校验准确率：0.62
第10轮，训练损失：0.65，校验损失：0.57，校验准确率：0.62
第10轮，训练损失：0.65，校验损失：0.57，校验准确率：0.62
第10轮，训练损失：0.65，校验损失：0.57，校验准确率：0.62
第10轮，训练损失：0.65，校验损失：0.57，校验准确率：0.62
第10轮，训练损失：0.65，校验损失：0.57，校验准确率：0.62
第10轮，训练损失：0.65，校验损失：0.57，校验准确率：0.62
第10轮，训练损失：0.65，校验损失：0.57，校验准确率：0.62
第10轮，训练损失：0.65，校验损失：0.57，校验准确率：0.62
第10轮，训练损失：0.65，校验损失：0.57，校验准确率：0.62
第10轮，训练损失：0.65，校验损失：0.57，校验准确率：0.62
第10轮，训练损失：0.65，校验损失：0.57，校验准确率：0.62
第10轮，训练损失：0.65，校验损失：0.57，校验准确率：0.62
第10轮，训练损失：0.65，校验损失：0.57，校验准确率：0.62
第10轮，训练损失：0.65，校验损失：0.57，校验准确率：0.62
第10轮，训练损失：0.65，校验损失：0.57，校验准确率：0.62
第10轮，训练损失：0.65，校验损失：0.57，校验准确率：0.62
第10轮，训练损失：0.65，校验损失：0.57，校验准确率：0.62
第10轮，训练损失：0.65，校验损失：0.57，校验准确率：0.62
第10轮，训练损失：0.65，校验损失：0.57，校验准确率：0.62
第10轮，训练损失：0.65，校验损失：0.58，校验准确率：0.62
第10轮，训练损失：0.65，校验损失：0.58，校验准确率：0.62
第10轮，训练损失：0.65，校验损失：0.58，校验准

第10轮，训练损失：0.65，校验损失：0.57，校验准确率：0.63
第10轮，训练损失：0.65，校验损失：0.57，校验准确率：0.63
第10轮，训练损失：0.65，校验损失：0.57，校验准确率：0.62
第10轮，训练损失：0.65，校验损失：0.57，校验准确率：0.62
第10轮，训练损失：0.65，校验损失：0.57，校验准确率：0.62
第10轮，训练损失：0.65，校验损失：0.57，校验准确率：0.62
第10轮，训练损失：0.65，校验损失：0.57，校验准确率：0.62
第10轮，训练损失：0.65，校验损失：0.57，校验准确率：0.62
第10轮，训练损失：0.65，校验损失：0.57，校验准确率：0.62
第10轮，训练损失：0.65，校验损失：0.57，校验准确率：0.62
第10轮，训练损失：0.65，校验损失：0.57，校验准确率：0.62
第10轮，训练损失：0.65，校验损失：0.57，校验准确率：0.62
第10轮，训练损失：0.65，校验损失：0.57，校验准确率：0.62
第10轮，训练损失：0.65，校验损失：0.57，校验准确率：0.62
第10轮，训练损失：0.65，校验损失：0.57，校验准确率：0.62
第10轮，训练损失：0.65，校验损失：0.57，校验准确率：0.62
第10轮，训练损失：0.65，校验损失：0.57，校验准确率：0.62
第10轮，训练损失：0.65，校验损失：0.57，校验准确率：0.62
第10轮，训练损失：0.65，校验损失：0.57，校验准确率：0.62
第10轮，训练损失：0.65，校验损失：0.57，校验准确率：0.62
第10轮，训练损失：0.65，校验损失：0.57，校验准确率：0.62
第10轮，训练损失：0.65，校验损失：0.57，校验准确率：0.62
第10轮，训练损失：0.65，校验损失：0.57，校验准确率：0.62
第10轮，训练损失：0.65，校验损失：0.57，校验准确率：0.62
第10轮，训练损失：0.65，校验损失：0.57，校验准确率：0.62
第10轮，训练损失：0.65，校验损失：0.57，校验准确率：0.62
第10轮，训练损失：0.65，校验损失：0.57，校验准确率：0.62
第10轮，训练损失：0.65，校验损失：0.57，校验准

In [63]:
vals=[]
for data,target in zip(test_data,test_label):
    data,target=torch.tensor(data,dtype=torch.float).view(1,-1),torch.tensor(np.array([target]),dtype=torch.long)
    output=model(data)
    val=rightness(output,target)
    vals.append(val)

rights=(sum([tup[0] for tup in vals]),sum([tup[1] for tup in vals]))
right_rate=1.0*rights[0].data.numpy()/rights[1]

In [64]:
right_rate

0.5927051671732523

In [65]:
model.named_parameters

<bound method Module.named_parameters of Sequential(
  (0): Linear(in_features=3948, out_features=10, bias=True)
  (1): ReLU()
  (2): Linear(in_features=10, out_features=2, bias=True)
  (3): LogSoftmax(dim=1)
)>